(heckman_code)=

# Heckman Code

The python code generating the toy data for the figures above is given
below. This version examines Case 4.[^fn1]

In [ ]:
# start a connected stata17 session
from pystata import config
config.init('be')

In [10]:
import numpy as np
import pandas as pd

# true parameters
rho_t = np.array([0.8])
rho_x_w_t = np.array([0.8])
gamma_t = np.array([.5,1.0])
beta_t = np.array([-2.0,0.5])
sigma_e_t = np.array([1.0])
N =5000

# generate toy data consistent with heckman:
# generate potentially correlated x,w data
mean_x_w = np.array([0,0])
cov_x_w = np.array([[1,rho_x_w_t[0]],[rho_x_w_t[0], 1]])
w, x = np.random.multivariate_normal(mean_x_w, cov_x_w, N).T

# add constant to first position and convert to DataFrame
w_ = pd.DataFrame(np.c_[np.ones(N),w],columns=['Constant (Selection)','Slope (Selection)'])
x_ = pd.DataFrame(np.c_[np.ones(N),x], columns=['Constant','Slope'])

# generate errors 
mean_u_eps = np.array([0,0])
cov_u_eps = np.array([[1,rho_t[0]],[rho_t[0],sigma_e_t[0]]])
u, epsilon = np.random.multivariate_normal(mean_u_eps, cov_u_eps, N).T

# generate latent zstar
zstar = w_.dot(gamma_t) + u
# generate observed z (indicator=1 if zstar is positive)
z = zstar > 0  

# generate latent ystar
ystar = x_.dot(beta_t) + epsilon
y=ystar.copy()
# generate observed y [if z=0, set y to NaN]
y[~z] = np.nan

stata_data = pd.DataFrame(np.c_[y,z,x,w], columns=['y','z','x','w'])
stata_data.head()

y    z         x         w
0 -2.174201  1.0 -0.034267  0.068906
1 -2.378358  1.0 -0.765331  0.495672
2       NaN  0.0 -0.952739 -1.519415
3 -2.380697  1.0 -1.453156 -0.074578
4  0.254649  1.0  0.180989  0.760963

We can estimate a Two-Step Heckman Model in Python using an [unmerged
branch](https://github.com/statsmodels/statsmodels/blob/92ea62232fd63c7b60c60bee4517ab3711d906e3/statsmodels/regression/heckman.py)
from StatsModels (this replicates the Stata two-step results).

In [12]:
import heckman as heckman
res = heckman.Heckman(y, x_, w_).fit(method='twostep')
print(res.summary())

       Heckman Regression Results      
Dep. Variable:                        y
Model:                          Heckman
Method:                Heckman Two-Step
Date:                  Wed, 12 May 2021
Time:                          12:19:08
No. Total Obs.:                    5000
No. Censored Obs.:                 1742
No. Uncensored Obs.:               3258
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Constant      -2.0018      0.035    -57.110      0.000      -2.071      -1.933
Slope          0.5187      0.023     22.543      0.000       0.474       0.564
                           coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------------------
Constant (Selection)     0.5567      0.022     25.017      0.000       0.513       0.600
Slope (Selection)        0.9959      0.028     35.566    

And in Stata, we can estimate the Full Information Maximum Likelihood
model over the toy dataset as

In [13]:
%%stata -d stata_data
heckman y x, select(z=w)


Iteration 0:   log likelihood = -6328.3022  
Iteration 1:   log likelihood = -6328.1976  
Iteration 2:   log likelihood = -6328.1976  

Heckman selection model                         Number of obs     =      5,000
(regression model with sample selection)              Selected    =      3,258
                                                      Nonselected =      1,742

                                                Wald chi2(1)      =     852.59
Log likelihood = -6328.198                      Prob > chi2       =     0.0000

------------------------------------------------------------------------------
             | Coefficient  Std. err.      z    P>|z|     [95% conf. interval]
-------------+----------------------------------------------------------------
y            |
           x |   .5220726   .0178798    29.20   0.000     .4870289    .5571163
       _cons |  -2.005327   .0219433   -91.39   0.000    -2.048335   -1.962319
-------------+------------------------------------------

[^fn1]: Note, we are using Stata 17 Jupyter Notebook integration using the `%%stata` magic.